In [ ]:
# Documentation gspread
# https://docs.gspread.org/en/latest/user-guide.html

import numpy as np
import pandas as pd
import seaborn as sns
import datetime


!pip install --upgrade -q gspread

import pandas as pd

from google.colab import auth
auth.authenticate_user()

import gspread
from google.auth import default
creds, _ = default()

gc = gspread.authorize(creds)


# Insert custom functions
!pip install pydrive                             # Package to use Google Drive API - not installed in Colab VM by default
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from oauth2client.client import GoogleCredentials

gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()

drive = GoogleDrive(gauth)
your_module = drive.CreateFile({"id": "1dizGN2VPwZ_GycmTgMXuh7tdos_mkSV5"})   # "your_module_file_id" is the part after "id=" in the shareable link
your_module.GetContentFile("funciones.py")          # Save the .py module file to Colab VM
import funciones as fun

# Load historical Data

t_sheet_url = "https://docs.google.com/spreadsheets/d/1pxSigN-tBbPKUZTv2GT_KrxQhWG5uYJ509ZmmDQsfQc/edit#gid=1858808857"
tab_name = "Train"

worksheet = gc.open_by_url(t_sheet_url)

df = pd.DataFrame.from_records( 
    worksheet.worksheet(tab_name).get_all_values(),
    )

df.columns = df.loc[0].values
df = df.iloc[ 1: ]

type_dic = {
    'bull' : int ,
    'D_MVA200': float , 
    'length': int , 
    'heigth': float , 
    'type': str , 
    'entry': float , 
    'stop': float , 
    'gain': int ,
    'target': float , 
    'stop_trade': float , 
    'resistance_support': str , 
    'MVA200_interact': int,
    'D_target': float,
    'D_stop_trade': float,
    'pair': str
}

df = df.astype( type_dic )

df.head()

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


date  bull  D_MVA200  length    heigth           type  \
1  2001-12-05 18:00:00     0 -1.004932      24  1.380822  Double Bottom   
2  2001-12-10 14:00:00     0 -0.780469      15  1.724340  Double Bottom   
3  2001-12-11 02:00:00     0  0.231401       6  0.356688     Double Top   
4  2001-12-18 22:00:00     0  3.738432       6  0.931116     Double Top   
5  2001-12-19 02:00:00     0  4.092700       4  1.183099  Double Bottom   

     entry     stop  gain    target  stop_trade resistance_support  \
1  0.88784  0.88424     1  0.897647    0.881633               none   
2  0.88834  0.88414     1  0.899176    0.881704               none   
3  0.89074  0.89154     0  0.886897    0.893783               none   
4  0.90124  0.90404     1  0.892633    0.907047              below   
5  0.90244  0.89884     0  0.912683    0.895797               none   

   MVA200_interact  D_target  D_stop_trade     pair  
1                0  3.761644      2.380822  EUR/USD  
2                0  4.448680      2.724340  EUR/USD  
3                0  1.713376      1.356688  EUR/USD  
4                0  2.862233      1.931116  EUR/USD  
5                0  3.366197      2.183099  EUR/USD

In [ ]:
import plotly.express as px

# Trade analysis on bull tendency
dfbull = df[ (df.bull == 1) & (df['type'] == 'Double Bottom') & (df.resistance_support == "over")]

px.scatter(
    dfbull,
    x = 'D_target',
    y = 'D_MVA200',
    color = dfbull['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "resistance_support",
    facet_row = "type"
)

In [ ]:
px.histogram(
    dfbull,
    x = 'type',
    color = dfbull['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    barmode='group',
    histfunc='count',
    facet_row = "MVA200_interact"
)

In [ ]:
dfbull.gain.value_counts()[1] / len( dfbull.gain )

0.3651459535046321

In [ ]:
# Trade analysis on bull tendency
nodfbull = df[ (df.bull == 0) & (df['type'] == 'Double Top') & (df.resistance_support == "below") ]

px.scatter(
    nodfbull,
    x = 'D_target',
    y = 'D_MVA200',
    color = nodfbull['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "resistance_support",
    facet_row = "type"
)

In [ ]:
px.histogram(
    nodfbull,
    x = 'type',
    color = nodfbull['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    barmode='group',
    histfunc='count',
    facet_row = "MVA200_interact"
)

In [ ]:
nodfbull.gain.value_counts()[1] / len( nodfbull.gain )

0.3647834274952919

In [ ]:
px.scatter(
    df,
    x = 'length',
    y = 'heigth',
    color = df['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "resistance_support",
    facet_row =  "type"
)

In [ ]:
px.histogram(
    df,
    x = 'type',
    color = df['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "resistance_support",
    facet_row = "MVA200_interact",
    barmode='group',
    histfunc='count'
)

In [ ]:
px.histogram(
    df,
    x = 'heigth',
    color = df['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "type",
    nbins = 20
)

In [ ]:
 testdf=df.tail(100)

 testdf[ testdf["type"] == "Double Top" ].tail()

date  bull  D_MVA200  length    heigth        type  \
100547  2019-12-11 22:00:00     1  7.943379      11  1.029973  Double Top   
100549  2019-12-12 14:00:00     1  7.584262       5  1.049655  Double Top   
100552  2019-12-18 22:00:00     1  4.259660       7  1.327826  Double Top   
100554  2019-12-20 18:00:00     1  4.774184      23  1.238067  Double Top   
100555  2019-12-23 02:00:00     1  5.925477       4  0.886076  Double Top   

          entry     stop  gain    target  stop_trade resistance_support  \
100547  0.86701  0.86917     0  0.860593    0.871267               none   
100549  0.86758  0.86986     0  0.860848    0.872032               none   
100552  0.86377  0.86664     0  0.855869    0.868801               none   
100554  0.86762  0.87064     0  0.859141    0.873079               none   
100555  0.86879  0.87064     0  0.863002    0.872728               none   

        MVA200_interact  D_target  D_stop_trade     pair  
100547                0  3.059946      2.029973  NZD/CAD  
100549                0  3.099309      2.049655  NZD/CAD  
100552                0  3.655651      2.327826  NZD/CAD  
100554                0  3.476135      2.238067  NZD/CAD  
100555                0  2.772152      1.886076  NZD/CAD

In [ ]:
px.histogram(
    nodfbull,
    x = 'D_MVA200',
    color = nodfbull['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "type",
    facet_row = "MVA200_interact",
    nbins = 20
)

In [ ]:
nodfbull[ (nodfbull.D_MVA200 < -0.015) & (nodfbull['type'] == "Double Top" ) ].gain.value_counts()[1]/ len( nodfbull[ (nodfbull.D_MVA200 < -0.015) & (nodfbull['type'] == "Double Top" ) ].gain )

0.3601871101871102

In [ ]:
px.histogram(
    dfbull,
    x = 'D_MVA200',
    color = dfbull['gain'].astype(str),
    color_discrete_map={
                "0": "red",
                "1": "blue"
                },
    category_orders={
        "gain": ["0", "1"]
        },
    facet_col = "type",
    facet_row = "MVA200_interact",
    nbins = 20
)

In [ ]:
print( dfbull[ (dfbull.D_MVA200 > 0.015) & (dfbull['type'] == "Double Bottom") ].gain.value_counts()[1]/ len(dfbull[ (dfbull.D_MVA200 > 0.015) & (dfbull['type'] == "Double Bottom") ].gain) , len(dfbull[ (dfbull.D_MVA200 > 0.015) & (dfbull['type'] == "Double Bottom") ].gain)) 

0.36955469506292354 4132


In [ ]:

df



date  bull  D_MVA200  length    heigth           type  \
1       2001-12-05 18:00:00     0 -1.004932      24  1.380822  Double Bottom   
2       2001-12-10 14:00:00     0 -0.780469      15  1.724340  Double Bottom   
3       2001-12-11 02:00:00     0  0.231401       6  0.356688     Double Top   
4       2001-12-18 22:00:00     0  3.738432       6  0.931116     Double Top   
5       2001-12-19 02:00:00     0  4.092700       4  1.183099  Double Bottom   
...                     ...   ...       ...     ...       ...            ...   
100552  2019-12-18 22:00:00     1  4.259660       7  1.327826     Double Top   
100553  2019-12-19 14:00:00     1  4.826174       7  2.072455  Double Bottom   
100554  2019-12-20 18:00:00     1  4.774184      23  1.238067     Double Top   
100555  2019-12-23 02:00:00     1  5.925477       4  0.886076     Double Top   
100556  2019-12-27 10:00:00     1  9.080220       4  1.393939  Double Bottom   

          entry     stop  gain    target  stop_trade resistance_support  \
1       0.88784  0.88424     1  0.897647    0.881633               none   
2       0.88834  0.88414     1  0.899176    0.881704               none   
3       0.89074  0.89154     0  0.886897    0.893783               none   
4       0.90124  0.90404     1  0.892633    0.907047              below   
5       0.90244  0.89884     0  0.912683    0.895797               none   
...         ...      ...   ...       ...         ...                ...   
100552  0.86377  0.86664     0  0.855869    0.868801               none   
100553  0.86604  0.86130     1  0.877807    0.859013               none   
100554  0.86762  0.87064     0  0.859141    0.873079               none   
100555  0.86879  0.87064     0  0.863002    0.872728               none   
100556  0.87601  0.87348     0  0.882885    0.871665               none   

        MVA200_interact  D_target  D_stop_trade     pair  
1                     0  3.761644      2.380822  EUR/USD  
2                     0  4.448680      2.724340  EUR/USD  
3                     0  1.713376      1.356688  EUR/USD  
4                     0  2.862233      1.931116  EUR/USD  
5                     0  3.366197      2.183099  EUR/USD  
...                 ...       ...           ...      ...  
100552                0  3.655651      2.327826  NZD/CAD  
100553                0  5.144909      3.072455  NZD/CAD  
100554                0  3.476135      2.238067  NZD/CAD  
100555                0  2.772152      1.886076  NZD/CAD  
100556                0  3.787879      2.393939  NZD/CAD  

[100556 rows x 16 columns]

In [ ]:
print( df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.sum() , df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.count() )
df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.sum() / df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.count()

1530 4143


0.36929761042722664

In [ ]:
# sin bull
print( df[ (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.sum() , df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.count() )
df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.sum() / df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.count()

1897 5226


0.36299272866437043

In [ ]:
# sin bull , resistance
print( df[ (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) ].gain.sum() , df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" )  ].gain.count() )
df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) ].gain.sum() / df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" )  ].gain.count()

9180 25892


0.35454966785107367

In [ ]:
# sin bull , resistance con MVA200_interact
print( df[ (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1) ].gain.sum() , df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1)  ].gain.count() )
df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1) ].gain.sum() / df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1) ].gain.count()

1747 4903


0.35631246175810727

In [ ]:
# sin bull , resistance , D_MVA200 con MVA200_interact
print(  
    df[(df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1) ].gain.sum() , 
    df[  (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1)  ].gain.count() 
    )

df[  (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1) ].gain.sum() / df[  (df['type'] == "Double Bottom" ) & (df.MVA200_interact == 1) ].gain.count()

1747 4903


0.35631246175810727

In [ ]:
# sin D_MVA200
print( 
    df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.sum() , 
    df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.count() 
    )
df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.sum() / df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support == "over" ) ].gain.count()

2089 5721


0.3651459535046321

In [ ]:
# sin resistance_support
print( 
    df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) ].gain.sum() , 
    df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) ].gain.count() 
    )

df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) ].gain.sum() / df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) ].gain.count()


7446 20784


0.35825635103926096

In [ ]:
# resistance_support != none
print( 
    df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() , 
    df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count() 
    )
df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() / df[ (df.bull == 1) & (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count()

1530 4143


0.36929761042722664

In [ ]:
# resistance_support != none sin bull
print( 
    df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() , 
    df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count() 
    )
df[  (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() / df[ (df.D_MVA200 > 0 ) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count()

1899 5229


0.36316695352839934

In [ ]:
# resistance_support != none sin D_MVA200
print( 
    df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() , 
    df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count() 
    )
df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() / df[ (df.bull == 1) & (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count()

2089 5721


0.3651459535046321

In [ ]:
# resistance_support != none sin D_MVA200 ,  bull
print( 
    df[ (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() , 
    df[ (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count() 
    )
df[ (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.sum() / df[ (df['type'] == "Double Bottom" ) & (df.resistance_support != "none" ) ].gain.count()

3033 8646


0.35079805690492716